# Library

In [ ]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
import seaborn as sns

import warnings
warnings.

AttributeError: module 'warnings' has no attribute 'filter'

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
os.chdir('/content/drive/MyDrive/스파르타_태블로(아마존)_프로젝트')
os.getcwd()

'/content/drive/MyDrive/스파르타_태블로(아마존)_프로젝트'

# Data read

In [ ]:
raw_data = pd.read_csv('./AmazonFoodCategory Dataset.csv')
print(raw_data.shape)

(65280, 20)


# 결측치

In [ ]:
df = raw_data.copy()
df.head(3)

Custkey     DateKey  Discount Amount Invoice Date  Invoice Number  \
0  10016609  12/31/2019           398.73   2019/12/31          329568   
1  10016609  12/31/2019           268.67   2019/12/31          329569   
2  10016609  12/31/2019           398.73   2019/12/31          329569   

  Item Class Item Number                        Item  Line Number  List Price  \
0        P01       15640         Super Vegetable Oil         1000      163.47   
1        P01       31681  Golden Fajita French Fries         7000      275.37   
2        P01       15640         Super Vegetable Oil         4000      163.47   

   Order Number Promised Delivery Date  Sales Amount  \
0        122380             12/31/2019        418.62   
1        123966             12/31/2019        282.07   
2        123966             12/31/2019        418.62   

   Sales Amount Based on List Price  Sales Cost Amount  Sales Margin Amount  \
0                            817.35             102.99               315.63   
1                            550.74             117.45               164.62   
2                            817.35             102.99               315.63   

   Sales Price  Sales Quantity  Sales Rep U/M  
0       83.724               5        176  EA  
1      141.035               2        176  EA  
2       83.724               5        176  EA

In [ ]:
null_df = pd.concat([df.isnull().sum(), df.isnull().sum() / len(df)], axis = 1)
null_df.columns = ['num', 'ratio']
null_df[null_df['num'] > 0]

num     ratio
Discount Amount     2  0.000031
Item Class       8285  0.126915
Item Number        40  0.000613
Sales Price         1  0.000015

In [ ]:
# 결측치 처리
# 1. Item Number, Item Class : 필요 없는 변수 (거의 모든 값이 P01) -> Custom 으로 Class 를 만들것
# 2. Discount Amount, Sales Price -> 행 삭제 (결측치 수가 적고)

# Item Number, Item Class 컬럼 제거
df.drop(['Item Number', 'Item Class'], axis = 1, inplace = True)

# Discount Amount, Sales Price 행 제거
df.dropna(inplace = True)

df.shape # 65,280 -> 65,278

(65278, 18)

In [ ]:
# 결측치 확인
null_df = pd.concat([df.isnull().sum(), df.isnull().sum() / len(df)], axis = 1)
null_df.columns = ['num', 'ratio']
null_df[null_df['num'] > 0]

Empty DataFrame
Columns: [num, ratio]
Index: []

# 이상치 및 데이터 클리닝
- Custom Item Class 추가
- Promised Delivery Date 가 DateKey 날짜보다 빠른 경우 DateKey 일자와 동일한 값으로 정리하기.
- U/M 동일 아이템명을 가진 데이터를 참고해서 변경 ('EA')

In [ ]:
# !pip install --upgrade -q gspread

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.5/57.5 kB 1.9 MB/s eta 0:00:00


## google sheet 불러오기

In [ ]:
import gspread
import google
from google.auth.transport.requests import Request
from google.colab import auth
from oauth2client.service_account import ServiceAccountCredentials

# 사용자 인증
auth.authenticate_user()

# 인증 스코프 설정 (Google Drive와 Google Sheets에 접근 권한)
scope = ['https://spreadsheets.google.com/feeds',
         'https://www.googleapis.com/auth/drive']

# 인증 정보 설정 (만약 Service Account 사용 시, JSON 키 파일을 사용해도 됩니다)
creds, _ = google.auth.default()
gc = gspread.authorize(creds)

In [ ]:
spreadsheet_id = '1XNZfBYFxlDGT_3Zr8bIk0h68uY3tng6NOYAGN70DSkg'

In [ ]:
# 스프레드시트 열기
sheet = gc.open_by_key(spreadsheet_id)

# 특정 시트 이름을 지정하여 불러오기
worksheet = sheet.worksheet('category_value(Custom)')

# 시트 데이터 가져오기 (전체 데이터를 가져올 때)
data = worksheet.get_all_values()

In [ ]:
# 데이터를 DataFrame으로 변환
custom_category = pd.DataFrame(data[1:], columns=data[0])

# 결측값 처리 (예시)
custom_category.fillna("N/A", inplace=True)

# 전처리된 데이터 확인
custom_category.head()

value               category
0     Washington Cranberry Juice  Beverages and Alcohol
1                     Token Cola  Beverages and Alcohol
2  BBB Best Creamy Peanut Butter  Condiments and Sauces
3             Club String Cheese         Dairy Products
4     Even Better Chocolate Milk         Dairy Products

## 1.Custom Item Class 추가

In [ ]:
df = pd.merge(df, custom_category, left_on = 'Item', right_on = 'value', how = 'left').drop(columns = ['value'])
df.head()

Custkey     DateKey  Discount Amount Invoice Date  Invoice Number  \
0  10016609  12/31/2019           398.73   2019/12/31          329568   
1  10016609  12/31/2019           268.67   2019/12/31          329569   
2  10016609  12/31/2019           398.73   2019/12/31          329569   
3  10016609  12/31/2019           466.45   2019/12/31          329569   
4  10016609  12/31/2019           515.51   2019/12/31          329569   

                         Item  Line Number  List Price  Order Number  \
0         Super Vegetable Oil         1000      163.47        122380   
1  Golden Fajita French Fries         7000      275.37        123966   
2         Super Vegetable Oil         4000      163.47        123966   
3            High Top Oranges         3000      119.52        123966   
4       Tell Tale New Potatos         9000      264.18        123966   

  Promised Delivery Date  Sales Amount  Sales Amount Based on List Price  \
0             12/31/2019        418.62                            817.35   
1             12/31/2019        282.07                            550.74   
2             12/31/2019        418.62                            817.35   
3             12/31/2019        489.71                            956.16   
4             12/31/2019        541.21                           1056.72   

   Sales Cost Amount  Sales Margin Amount  Sales Price  Sales Quantity  \
0             102.99               315.63     83.72400               5   
1             117.45               164.62    141.03500               2   
2             102.99               315.63     83.72400               5   
3             213.29               276.42     61.21375               8   
4             290.56               250.65    135.30250               4   

   Sales Rep U/M               category  
0        176  EA                    Oil  
1        176  EA     Snacks and Cookies  
2        176  EA                    Oil  
3        176  EA  Vegetables and Fruits  
4        176  EA  Vegetables and Fruits

## 2. Promised Delivery Date 가 DateKey 날짜보다 빠른 경우 DateKey 일자와 동일한 값으로 정리하기.

In [ ]:
# DateKey와 Promised Delivery Date가 DateTime 형식으로 되어 있어야 비교가 가능
# 만약 문자열로 되어 있다면, DateTime으로 변환
df['DateKey'] = pd.to_datetime(df['DateKey'])
df['Promised Delivery Date'] = pd.to_datetime(df['Promised Delivery Date'])

In [ ]:
# Promised Delivery Date가 DateKey보다 빠른 경우 필터링
invalid_dates = df[df['Promised Delivery Date'] < df['DateKey']]

# 그런 경우들이 몇 개인지 보여줌
print(f"Promised Delivery Date가 DateKey보다 빠른 경우는 {len(invalid_dates)}개입니다.")

Promised Delivery Date가 DateKey보다 빠른 경우는 8968개입니다.


In [ ]:
# Promised Delivery Date가 DateKey보다 빠른 경우, Promised Delivery Date를 DateKey와 동일하게 변경
df.loc[df['Promised Delivery Date'] < df['DateKey'], 'Promised Delivery Date'] = df['DateKey']

# 변경 후 확인
print("변경 완료!")
df.head()  # df에서 변경된 결과 일부 확인

변경 완료!


Custkey    DateKey  Discount Amount Invoice Date  Invoice Number  \
0  10016609 2019-12-31           398.73   2019/12/31          329568   
1  10016609 2019-12-31           268.67   2019/12/31          329569   
2  10016609 2019-12-31           398.73   2019/12/31          329569   
3  10016609 2019-12-31           466.45   2019/12/31          329569   
4  10016609 2019-12-31           515.51   2019/12/31          329569   

                         Item  Line Number  List Price  Order Number  \
0         Super Vegetable Oil         1000      163.47        122380   
1  Golden Fajita French Fries         7000      275.37        123966   
2         Super Vegetable Oil         4000      163.47        123966   
3            High Top Oranges         3000      119.52        123966   
4       Tell Tale New Potatos         9000      264.18        123966   

  Promised Delivery Date  Sales Amount  Sales Amount Based on List Price  \
0             2019-12-31        418.62                            817.35   
1             2019-12-31        282.07                            550.74   
2             2019-12-31        418.62                            817.35   
3             2019-12-31        489.71                            956.16   
4             2019-12-31        541.21                           1056.72   

   Sales Cost Amount  Sales Margin Amount  Sales Price  Sales Quantity  \
0             102.99               315.63     83.72400               5   
1             117.45               164.62    141.03500               2   
2             102.99               315.63     83.72400               5   
3             213.29               276.42     61.21375               8   
4             290.56               250.65    135.30250               4   

   Sales Rep U/M               category  
0        176  EA                    Oil  
1        176  EA     Snacks and Cookies  
2        176  EA                    Oil  
3        176  EA  Vegetables and Fruits  
4        176  EA  Vegetables and Fruits

## 3. U/M 동일 아이템명을 가진 데이터를 참고해서 변경 ('EA')

In [ ]:
# U/M value count
df['U/M'].value_counts()

U/M
EA    58989
SE     5629
PR      659
-         1
Name: count, dtype: int64

In [ ]:
# '-' 값이 있는 행 찾기
invalid_um_rows = df[df['U/M'] == '-']

# 동일한 Item에 대한 UM 값으로 대체
for idx, row in invalid_um_rows.iterrows():
    # 동일한 Item의 다른 행에서 UM 값을 찾음
    correct_um = df[(df['Item'] == row['Item']) & (df['U/M'] != '-')]['U/M'].values
    if len(correct_um) > 0:
        # 첫 번째로 발견된 UM 값으로 대체
        df.at[idx, 'U/M'] = correct_um[0]



In [ ]:
# U/M value count
df['U/M'].value_counts()

U/M
EA    58990
SE     5629
PR      659
Name: count, dtype: int64

## 2018년 데이터 제거

In [ ]:
df = df[df['DateKey'].dt.year != 2018]

# 잘 처리되었는지 확인
# 2018년 데이터 제거
df_filtered = df[df['DateKey'].dt.year != 2018]

# 2018년 데이터가 제거되었는지 확인 (2018년 데이터가 존재하지 않아야 함)
if df_filtered[df_filtered['DateKey'].dt.year == 2018].empty:
    print("2018년 데이터가 성공적으로 제거되었습니다.")
else:
    print("2018년 데이터가 여전히 존재합니다.")

2018년 데이터가 성공적으로 제거되었습니다.


## 공휴일 변수 추가

In [ ]:
# !pip install holidays
import holidays

In [ ]:
# 2017년도 미국 공휴일 리스트 생성
us_holidays = holidays.US(years=[2017, 2019])

# 공휴일 여부를 확인하는 함수
def is_holiday(date):
    return date in us_holidays

# 공휴일 이름을 반환하는 함수
def get_holiday_name(date):
    return us_holidays.get(date) if date in us_holidays else None

# 'IsHoliday' 컬럼 추가 (True/False)
df['IsHoliday'] = df['DateKey'].apply(is_holiday)

# 'HolidayName' 컬럼 추가 (공휴일 이름)
df['HolidayName'] = df['DateKey'].apply(get_holiday_name)

In [ ]:
# 공휴일인 행만 필터링
holiday_df = df[df['IsHoliday'] == True]
print(holiday_df.shape)
holiday_df.head(1)

(1732, 21)


Custkey    DateKey  Discount Amount Invoice Date  Invoice Number  \
4357  10000456 2019-11-11           839.73   2019/11/11          317176   

             Item  Line Number  List Price  Order Number  \
4357  Ebony Plums        23000      189.27        106394   

     Promised Delivery Date  ...  Sales Amount Based on List Price  \
4357             2019-11-11  ...                           1703.43   

      Sales Cost Amount  Sales Margin Amount  Sales Price  Sales Quantity  \
4357             476.15               387.55    95.966667               9   

      Sales Rep  U/M               category IsHoliday   HolidayName  
4357        163   EA  Vegetables and Fruits      True  Veterans Day  

[1 rows x 21 columns]

In [ ]:
# 공휴일 날짜의 고유한 값 추출
unique_holiday_dates = holiday_df['DateKey'].unique()
unique_holiday_name = holiday_df['HolidayName'].unique()

# 결과 출력
print("Unique Holiday Dates:")
print(unique_holiday_dates)

# 공휴일 데이터와 공휴일 이름 확인
print("\nHoliday Name:")
print(unique_holiday_name)

Unique Holiday Dates:
<DatetimeArray>
['2019-11-11 00:00:00', '2019-10-14 00:00:00', '2019-09-02 00:00:00',
 '2019-05-27 00:00:00', '2019-02-18 00:00:00', '2019-01-21 00:00:00',
 '2017-12-25 00:00:00', '2017-11-11 00:00:00', '2017-11-10 00:00:00',
 '2017-10-09 00:00:00', '2017-09-04 00:00:00', '2017-05-29 00:00:00',
 '2017-02-20 00:00:00', '2017-01-16 00:00:00', '2017-01-02 00:00:00',
 '2017-01-01 00:00:00']
Length: 16, dtype: datetime64[ns]

Holiday Name:
['Veterans Day' 'Columbus Day' 'Labor Day' 'Memorial Day'
 "Washington's Birthday" 'Martin Luther King Jr. Day' 'Christmas Day'
 'Veterans Day (observed)' "New Year's Day (observed)" "New Year's Day"]


## 고객별 누계 (3, 5, 7) stage 라벨 부여 + 기준점 출력

In [ ]:
df = pd.read_csv('preprocessed_data.csv')

In [ ]:
df['DateKey'] = pd.to_datetime(df['DateKey'])

## 카테고리별 누계 (3, 5, 7) stage 라벨 부여

In [ ]:
import pandas as pd

# 경계값들을 저장할 빈 리스트 생성
boundary_dict = {}

# 고객별 Sales Amount 누계
df_customer_sum = df.groupby('Custkey')['Sales Amount'].sum().reset_index()

# 3개, 5개, 7개 그룹화하여 라벨링 및 경계값 저장
df_customer_sum['Sales_3_Group'], bins_3 = pd.qcut(df_customer_sum['Sales Amount'], q=3, labels=[1, 2, 3], retbins=True)
df_customer_sum['Sales_5_Group'], bins_5 = pd.qcut(df_customer_sum['Sales Amount'], q=5, labels=[1, 2, 3, 4, 5], retbins=True)
df_customer_sum['Sales_7_Group'], bins_7 = pd.qcut(df_customer_sum['Sales Amount'], q=7, labels=[1, 2, 3, 4, 5, 6, 7], retbins=True)

# 경계값 저장
boundary_dict['Customer_3_Groups'] = bins_3
boundary_dict['Customer_5_Groups'] = bins_5
boundary_dict['Customer_7_Groups'] = bins_7

# 고객별 누계 정보를 원래 df에 병합
df = pd.merge(df, df_customer_sum[['Custkey', 'Sales_3_Group', 'Sales_5_Group', 'Sales_7_Group']], on='Custkey', how='left')

# 2017년 데이터 처리
df_2017 = df[df['DateKey'].dt.year == 2017]
df_customer_sum_2017 = df_2017.groupby('Custkey')['Sales Amount'].sum().reset_index()

df_customer_sum_2017['Sales_3_Group_2017'], bins_3_2017 = pd.qcut(df_customer_sum_2017['Sales Amount'], q=3, labels=[1, 2, 3], retbins=True)
df_customer_sum_2017['Sales_5_Group_2017'], bins_5_2017 = pd.qcut(df_customer_sum_2017['Sales Amount'], q=5, labels=[1, 2, 3, 4, 5], retbins=True)
df_customer_sum_2017['Sales_7_Group_2017'], bins_7_2017 = pd.qcut(df_customer_sum_2017['Sales Amount'], q=7, labels=[1, 2, 3, 4, 5, 6, 7], retbins=True)

# 경계값 저장
boundary_dict['Customer_3_Groups_2017'] = bins_3_2017
boundary_dict['Customer_5_Groups_2017'] = bins_5_2017
boundary_dict['Customer_7_Groups_2017'] = bins_7_2017

# 2017년 고객별 누계 정보를 원래 df에 병합
df = pd.merge(df, df_customer_sum_2017[['Custkey', 'Sales_3_Group_2017', 'Sales_5_Group_2017', 'Sales_7_Group_2017']], on='Custkey', how='left')

# 2019년 데이터 처리
df_2019 = df[df['DateKey'].dt.year == 2019]
df_customer_sum_2019 = df_2019.groupby('Custkey')['Sales Amount'].sum().reset_index()

df_customer_sum_2019['Sales_3_Group_2019'], bins_3_2019 = pd.qcut(df_customer_sum_2019['Sales Amount'], q=3, labels=[1, 2, 3], retbins=True)
df_customer_sum_2019['Sales_5_Group_2019'], bins_5_2019 = pd.qcut(df_customer_sum_2019['Sales Amount'], q=5, labels=[1, 2, 3, 4, 5], retbins=True)
df_customer_sum_2019['Sales_7_Group_2019'], bins_7_2019 = pd.qcut(df_customer_sum_2019['Sales Amount'], q=7, labels=[1, 2, 3, 4, 5, 6, 7], retbins=True)

# 경계값 저장
boundary_dict['Customer_3_Groups_2019'] = bins_3_2019
boundary_dict['Customer_5_Groups_2019'] = bins_5_2019
boundary_dict['Customer_7_Groups_2019'] = bins_7_2019

# 2019년 고객별 누계 정보를 원래 df에 병합
df = pd.merge(df, df_customer_sum_2019[['Custkey', 'Sales_3_Group_2019', 'Sales_5_Group_2019', 'Sales_7_Group_2019']], on='Custkey', how='left')

In [ ]:
df.head(3)

Custkey    DateKey  Discount Amount Invoice Date  Invoice Number  \
0  10016609 2019-12-31           398.73   2019/12/31          329568   
1  10016609 2019-12-31           268.67   2019/12/31          329569   
2  10016609 2019-12-31           398.73   2019/12/31          329569   

                         Item  Line Number  List Price  Order Number  \
0         Super Vegetable Oil         1000      163.47        122380   
1  Golden Fajita French Fries         7000      275.37        123966   
2         Super Vegetable Oil         4000      163.47        123966   

  Promised Delivery Date  ...  HolidayName  Sales_3_Group  Sales_5_Group  \
0             2019-12-31  ...          NaN              2              3   
1             2019-12-31  ...          NaN              2              3   
2             2019-12-31  ...          NaN              2              3   

   Sales_7_Group  Sales_3_Group_2017  Sales_5_Group_2017  Sales_7_Group_2017  \
0              4                   1                   1                   1   
1              4                   1                   1                   1   
2              4                   1                   1                   1   

  Sales_3_Group_2019 Sales_5_Group_2019  Sales_7_Group_2019  
0                  2                  4                   5  
1                  2                  4                   5  
2                  2                  4                   5  

[3 rows x 30 columns]

In [ ]:
# 카테고리별 Sales Amount 누계
df_category_sum = df.groupby('category')['Sales Amount'].sum().reset_index()

df_category_sum['Sales_3_Group_cat'], bins_category_3 = pd.qcut(df_category_sum['Sales Amount'], q=3, labels=[1, 2, 3], retbins=True)
df_category_sum['Sales_5_Group_cat'], bins_category_5 = pd.qcut(df_category_sum['Sales Amount'], q=5, labels=[1, 2, 3, 4, 5], retbins=True)
df_category_sum['Sales_7_Group_cat'], bins_category_7 = pd.qcut(df_category_sum['Sales Amount'], q=7, labels=[1, 2, 3, 4, 5, 6, 7], retbins=True)

# 경계값 저장
boundary_dict['Category_3_Groups_cat'] = bins_category_3
boundary_dict['Category_5_Groups_cat'] = bins_category_5
boundary_dict['Category_7_Groups_cat'] = bins_category_7

# 카테고리별 누계 정보를 원래 df에 병합
df = pd.merge(df, df_category_sum[['category', 'Sales_3_Group_cat', 'Sales_5_Group_cat', 'Sales_7_Group_cat']], on='category', how='left')

# 2017년 카테고리별 처리
df_category_2017 = df[df['DateKey'].dt.year == 2017].groupby('category')['Sales Amount'].sum().reset_index()

df_category_2017['Sales_3_Group_2017_cat'], bins_category_3_2017 = pd.qcut(df_category_2017['Sales Amount'], q=3, labels=[1, 2, 3], retbins=True)
df_category_2017['Sales_5_Group_2017_cat'], bins_category_5_2017 = pd.qcut(df_category_2017['Sales Amount'], q=5, labels=[1, 2, 3, 4, 5], retbins=True)
df_category_2017['Sales_7_Group_2017_cat'], bins_category_7_2017 = pd.qcut(df_category_2017['Sales Amount'], q=7, labels=[1, 2, 3, 4, 5, 6, 7], retbins=True)

# 경계값 저장
boundary_dict['Category_3_Groups_2017_cat'] = bins_category_3_2017
boundary_dict['Category_5_Groups_2017_cat'] = bins_category_5_2017
boundary_dict['Category_7_Groups_2017_cat'] = bins_category_7_2017

# 2017년 카테고리별 정보를 원래 df에 병합
df = pd.merge(df, df_category_2017[['category', 'Sales_3_Group_2017_cat', 'Sales_5_Group_2017_cat', 'Sales_7_Group_2017_cat']], on='category', how='left')

# 2019년 카테고리별 처리
df_category_2019 = df[df['DateKey'].dt.year == 2019].groupby('category')['Sales Amount'].sum().reset_index()

df_category_2019['Sales_3_Group_2019_cat'], bins_category_3_2019 = pd.qcut(df_category_2019['Sales Amount'], q=3, labels=[1, 2, 3], retbins=True)
df_category_2019['Sales_5_Group_2019_cat'], bins_category_5_2019 = pd.qcut(df_category_2019['Sales Amount'], q=5, labels=[1, 2, 3, 4, 5], retbins=True)
df_category_2019['Sales_7_Group_2019_cat'], bins_category_7_2019 = pd.qcut(df_category_2019['Sales Amount'], q=7, labels=[1, 2, 3, 4, 5, 6, 7], retbins=True)

# 경계값 저장
boundary_dict['Category_3_Groups_2019'] = bins_category_3_2019
boundary_dict['Category_5_Groups_2019'] = bins_category_5_2019
boundary_dict['Category_7_Groups_2019'] = bins_category_7_2019

# 2019년 카테고리별 정보를 원래 df에 병합
df = pd.merge(df, df_category_2019[['category', 'Sales_3_Group_2019_cat', 'Sales_5_Group_2019_cat', 'Sales_7_Group_2019_cat']], on='category', how='left')

In [ ]:
df.head()

Custkey    DateKey  Discount Amount Invoice Date  Invoice Number  \
0  10016609 2019-12-31           398.73   2019/12/31          329568   
1  10016609 2019-12-31           268.67   2019/12/31          329569   
2  10016609 2019-12-31           398.73   2019/12/31          329569   
3  10016609 2019-12-31           466.45   2019/12/31          329569   
4  10016609 2019-12-31           515.51   2019/12/31          329569   

                         Item  Line Number  List Price  Order Number  \
0         Super Vegetable Oil         1000      163.47        122380   
1  Golden Fajita French Fries         7000      275.37        123966   
2         Super Vegetable Oil         4000      163.47        123966   
3            High Top Oranges         3000      119.52        123966   
4       Tell Tale New Potatos         9000      264.18        123966   

  Promised Delivery Date  ...  Sales_7_Group_2019  Sales_3_Group_cat  \
0             2019-12-31  ...                   5                  1   
1             2019-12-31  ...                   5                  3   
2             2019-12-31  ...                   5                  1   
3             2019-12-31  ...                   5                  3   
4             2019-12-31  ...                   5                  3   

   Sales_5_Group_cat  Sales_7_Group_cat  Sales_3_Group_2017_cat  \
0                  1                  1                       1   
1                  5                  7                       3   
2                  1                  1                       1   
3                  5                  7                       3   
4                  5                  7                       3   

   Sales_5_Group_2017_cat  Sales_7_Group_2017_cat Sales_3_Group_2019_cat  \
0                       1                       1                      1   
1                       5                       7                      3   
2                       1                       1                      1   
3                       5                       7                      3   
4                       5                       7                      3   

  Sales_5_Group_2019_cat  Sales_7_Group_2019_cat  
0                      1                       1  
1                      5                       7  
2                      1                       1  
3                      5                       7  
4                      5                       7  

[5 rows x 39 columns]

## 누계 경계값 출력

In [ ]:
# 지수 표기법을 사용하지 않도록 설정
pd.set_option('display.float_format', '{:.2f}'.format)

# 경계값 딕셔너리를 DataFrame으로 변환
boundary_df = pd.DataFrame({key: pd.Series(value) for key, value in boundary_dict.items()})
boundary_df

Customer_3_Groups  Customer_5_Groups  Customer_7_Groups  \
0             203.31             203.31             203.31   
1           18007.79            7538.98            3948.15   
2          127291.26           30756.44           13722.38   
3        11397206.36           94412.61           35910.85   
4                NaN          270716.59           80447.40   
5                NaN        11397206.36          155440.40   
6                NaN                NaN          412705.31   
7                NaN                NaN        11397206.36   

   Customer_3_Groups_2017  Customer_5_Groups_2017  Customer_7_Groups_2017  \
0                  203.31                  203.31                  203.31   
1                 8188.26                 2430.88                 1514.36   
2                59218.78                13069.00                 5934.28   
3             11313868.49                41531.40                14184.11   
4                     NaN               142154.02                36088.74   
5                     NaN             11313868.49                81529.27   
6                     NaN                     NaN               199877.34   
7                     NaN                     NaN             11313868.49   

   Customer_3_Groups_2019  Customer_5_Groups_2019  Customer_7_Groups_2019  \
0                  215.57                  215.57                  215.57   
1                13110.00                 4999.44                 2936.88   
2                81945.25                16840.22                 9464.40   
3             10196927.89                52242.63                21289.67   
4                     NaN               167798.89                46236.19   
5                     NaN             10196927.89               107772.18   
6                     NaN                     NaN               263436.21   
7                     NaN                     NaN             10196927.89   

   Category_3_Groups_cat  Category_5_Groups_cat  Category_7_Groups_cat  \
0              219667.57              219667.57              219667.57   
1             7906157.13             6385440.48             5289053.07   
2            10993708.64             8783210.30             7699966.56   
3            38608120.11            10091335.86             9369228.22   
4                    NaN            24934282.99            10052725.77   
5                    NaN            38608120.11            12334502.83   
6                    NaN                    NaN            28760452.49   
7                    NaN                    NaN            38608120.11   

   Category_3_Groups_2017_cat  Category_5_Groups_2017_cat  \
0                   113681.13                   113681.13   
1                  4167398.72                  3390721.15   
2                  5778858.09                  4644240.34   
3                 20625767.66                  5342253.32   
4                         NaN                 12982729.43   
5                         NaN                 20625767.66   
6                         NaN                         NaN   
7                         NaN                         NaN   

   Category_7_Groups_2017_cat  Category_3_Groups_2019  Category_5_Groups_2019  \
0                   113681.13               105986.44               105986.44   
1                  2801036.06              3738758.41              2994719.33   
2                  4050939.24              5214850.55              4108292.99   
3                  4960671.87             17982352.45              4779759.51   
4                  5333231.23                     NaN             11951553.56   
5                  6446907.10                     NaN             17982352.45   
6                 15128424.04                     NaN                     NaN   
7                 20625767.66                     NaN                     NaN   

   Category_7_Groups_2019  
0               105986.44  
1              2488017.01  
2              3649027.32

# 데이터 저장

In [ ]:
df.to_csv('preprocessed_data.csv', index = False)
boundary_df.to_csv('boundary.csv', index = False)